In [1]:
import os
import numpy as np
import tifffile as tiff
import matplotlib.pyplot as plt
from skimage.transform import iradon, iradon_sart
from tqdm import tqdm
import random
import torch
import torch.nn.functional as F
import time

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

def load_metadata(file_path):
    metadata = {}
    with open(file_path, 'r') as file:
        current_section = None
        for line in file:
            line = line.strip()
            if line.startswith('[') and line.endswith(']'):
                current_section = line[1:-1]
                metadata[current_section] = {}
            elif '=' in line:
                key, value = line.split('=')
                metadata[current_section][key.strip()] = value.strip()
    return metadata

def load_projection_images(directory):
    image_files = sorted([f for f in os.listdir(directory) if f.endswith('.tif')])
    for file in tqdm(image_files, desc="Loading Projection Images"):
        image = tiff.imread(os.path.join(directory, file)).astype(np.float32)  # Convert to float32
        yield torch.tensor(image, dtype=torch.float32).to(device)

metadata_file_path = os.path.join(os.getcwd(), '20220811_chicken_bone_dose_10', '20220811_chicken_bone_dose_10_.txt')
projections_directory = os.path.join(os.getcwd(), '20220811_chicken_bone_dose_10', 'projections')

metadata = load_metadata(metadata_file_path)

# Normalize projections slice-by-slice
projections_generator = load_projection_images(projections_directory)
normalized_projections = []
max_value = torch.tensor(0.0).to(device)

for projection in projections_generator:
    max_value = torch.max(max_value, torch.max(projection))

projections_generator = load_projection_images(projections_directory)
for projection in projections_generator:
    normalized_projection = projection / max_value
    normalized_projections.append(normalized_projection.cpu().numpy())

# Convert to PyTorch tensor and move to GPU
projections = torch.tensor(np.array(normalized_projections), dtype=torch.float32).to(device)
del normalized_projections  # Free up memory

print("Loaded metadata:")
print(metadata)
print("Loaded projections shape:", projections.shape)

def preprocess_projections(projections):
    sinograms = torch.transpose(projections, 0, 1)
    print("Processed sinograms shape:", sinograms.shape)
    return sinograms

def fbp_reconstruction(sinogram, angles):
    sinogram_np = sinogram.cpu().numpy()
    reconstruction_fbp = iradon(sinogram_np, theta=angles, circle=True)
    return torch.tensor(reconstruction_fbp, dtype=torch.float32).to(device)

def sart_reconstruction(sinogram, angles, num_iterations=2):
    sinogram_np = sinogram.cpu().numpy()
    reconstruction_sart = iradon_sart(sinogram_np, theta=angles)
    for _ in tqdm(range(num_iterations - 1), desc="SART Iterations"):
        reconstruction_sart = iradon_sart(sinogram_np, theta=angles, image=reconstruction_sart)
    return torch.tensor(reconstruction_sart, dtype=torch.float32).to(device)

def reconstruct_full_volume(projections, angles, method='fbp'):
    num_slices = projections.shape[1]  # Number of slices to reconstruct
    reconstructed_volume = []
    for i in tqdm(range(num_slices), desc="Reconstructing full 3D volume"):
        slice_projections = projections[:, i, :]
        print(f"Slice {i}: slice_projections shape: {slice_projections.shape}")
        sinogram = preprocess_projections(slice_projections)
        if sinogram.ndim != 2:
            raise ValueError(f"Sinogram must be 2D, got {sinogram.ndim}D")
        if method == 'fbp':
            reconstructed_slice = fbp_reconstruction(sinogram, angles)
        elif method == 'sart':
            reconstructed_slice = sart_reconstruction(sinogram, angles)
        reconstructed_volume.append(reconstructed_slice.cpu().numpy())
    return np.array(reconstructed_volume)

angles = np.linspace(0, 360, int(metadata['ACQUISITION']['NumberImages']), endpoint=False)

# Measure time for FBP reconstruction
start_time = time.time()
reconstructed_volume_fbp = reconstruct_full_volume(projections, angles, method='fbp')
fbp_time = time.time() - start_time
print(f"FBP reconstruction time: {fbp_time:.2f} seconds")

# Measure time for SART reconstruction
start_time = time.time()
reconstructed_volume_sart = reconstruct_full_volume(projections, angles, method='sart')
sart_time = time.time() - start_time
print(f"SART reconstruction time: {sart_time:.2f} seconds")

def visualize_3d_volume(volume, num_random_slices=4):
    fig, axes = plt.subplots(2, 3, figsize=(18, 10))

    # Display middle slice along each axis
    axes[0, 0].imshow(volume[volume.shape[0] // 2, :, :], cmap='gray')
    axes[0, 0].set_title('Middle slice along axis 0')

    axes[0, 1].imshow(volume[:, volume.shape[1] // 2, :], cmap='gray')
    axes[0, 1].set_title('Middle slice along axis 1')

    axes[0, 2].imshow(volume[:, :, volume.shape[2] // 2], cmap='gray')
    axes[0, 2].set_title('Middle slice along axis 2')

    # Display random slices
    random_slices = random.sample(range(volume.shape[0]), num_random_slices)
    for i, slice_idx in enumerate(random_slices):
        axes[1, i].imshow(volume[slice_idx, :, :], cmap='gray')
        axes[1, i].set_title(f'Random slice {slice_idx}')

    plt.tight_layout()
    plt.show()

np.save('reconstructed_volume_fbp.npy', reconstructed_volume_fbp)
visualize_3d_volume(reconstructed_volume_fbp)
np.save('reconstructed_volume_sart.npy', reconstructed_volume_sart)
visualize_3d_volume(reconstructed_volume_sart)

# Print timing comparison
print(f"FBP reconstruction time: {fbp_time:.2f} seconds")
print(f"SART reconstruction time: {sart_time:.2f} seconds")

Loading Projection Images: 100%|██████████████████████████████████████████████████████████████████████████████████████████| 361/361 [00:07<00:00, 49.12it/s]


Loaded metadata:
{'GENERAL': {'ProjectName': '20220811_chicken_bone_dose_10_', 'Scanner': 'University of Helsinki Industrial Mathematics Computed Tomography Laboratory', 'Measurers': 'Alexander Meaney', 'Date': '20220811', 'DateFormat': 'YYYYMMDD'}, 'GEOMETRY': {'GeometryType': 'Cone', 'DistanceSourceDetector': '553.74', 'DistanceSourceOrigin': '210.66', 'DistanceUnit': 'mm'}, 'ACQUISITION': {'NumberImages': '361', 'AngleFirst': '0', 'AngleInterval': '1', 'AngleLast': '360'}, 'DETECTOR': {'Detector': 'Hamamatsu Photonics C7942CA-22', 'DetectorType': 'EID', 'Binning': '1x1', 'PixelSize': '0.050', 'PixelSizeUnit': 'mm', 'ExposureTime': '1000', 'ExposureTimeUnit': 'ms'}, 'XRAY': {'Tube': 'Oxford Instruments XTF5011', 'Target': 'Mo', 'Voltage': '40', 'VoltageUnit': 'kV', 'Current': '0.2', 'CurrentUnit': 'mA', 'XRayFilter': 'Al', 'XRayFilterThickness': '0.5', 'XRayFilterThicknessUnit': 'mm'}}
Loaded projections shape: torch.Size([361, 2368, 2240])


Reconstructing full 3D volume:   0%|                                                                                               | 0/2368 [00:00<?, ?it/s]

Slice 0: slice_projections shape: torch.Size([361, 2240])
Processed sinograms shape: torch.Size([2240, 361])


Reconstructing full 3D volume:   0%|                                                                                    | 1/2368 [00:36<23:47:41, 36.19s/it]

...


Reconstructing full 3D volume: 100%|██████████████████████████████████████████████████████████████████████████████▉| 2367/2368 [236:36:20<05:33, 333.33s/it]

Slice 2367: slice_projections shape: torch.Size([361, 2240])
Processed sinograms shape: torch.Size([2240, 361])



Reconstructing full 3D volume: 100%|███████████████████████████████████████████████████████████████████████████████| 2368/2368 [236:41:54<00:00, 359.85s/it]


SART reconstruction time: 852135.82 seconds


IndexError: index 3 is out of bounds for axis 1 with size 3

In [3]:
def visualize_3d_volume(volume, method_name, num_random_slices=4):
    num_random_slices = min(num_random_slices, 3)  # Limit the number of random slices to 3

    fig, axes = plt.subplots(2, 3, figsize=(18, 10))

    # Display middle slice along each axis
    axes[0, 0].imshow(volume[volume.shape[0] // 2, :, :], cmap='gray')
    axes[0, 0].set_title(f'Middle slice along axis 0 ({method_name})')

    axes[0, 1].imshow(volume[:, volume.shape[1] // 2, :], cmap='gray')
    axes[0, 1].set_title(f'Middle slice along axis 1 ({method_name})')

    axes[0, 2].imshow(volume[:, :, volume.shape[2] // 2], cmap='gray')
    axes[0, 2].set_title(f'Middle slice along axis 2 ({method_name})')

    # Display random slices
    random_slices = random.sample(range(volume.shape[0]), num_random_slices)
    for i, slice_idx in enumerate(random_slices):
        axes[1, i].imshow(volume[slice_idx, :, :], cmap='gray')
        axes[1, i].set_title(f'Random slice {slice_idx} ({method_name})')

    plt.tight_layout()
    plt.show()

np.save('reconstructed_volume_fbp.npy', reconstructed_volume_fbp)
visualize_3d_volume(reconstructed_volume_fbp, "FBP")
np.save('reconstructed_volume_sart.npy', reconstructed_volume_sart)
visualize_3d_volume(reconstructed_volume_sart, "SART")

In [5]:
def format_time(seconds):
    hrs, rem = divmod(seconds, 3600)
    mins, secs = divmod(rem, 60)
    return f"{int(hrs)} hrs {int(mins)} mins {secs:.2f} seconds"

In [6]:
# Print timing comparison in hh:mm:ss format
print(f"FBP reconstruction time: {format_time(fbp_time)}")
print(f"SART reconstruction time: {format_time(sart_time)}")

FBP reconstruction time: 21 hrs 18 mins 33.55 seconds
SART reconstruction time: 236 hrs 42 mins 15.82 seconds
